In [ ]:
!pip install mlflow 

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 25.8/25.8 MB 23.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 105.4/105.4 kB 5.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 147.8/147.8 kB 20.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 78.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 705.5/705.5 kB 46.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.3/207.3 kB 23.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 107.0/107.0 kB 14.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.2/44.2 kB 2.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.0/233.0 kB 27.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.7/101.7 kB 17.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 128.2/128.2 kB 19.5 MB/s e

In [ ]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report, roc_auc_score
import mlflow
import mlflow.sklearn
import pyspark.sql.functions as F
from pyspark.sql.types import DoubleType, IntegerType

# Enable autologging
mlflow.sklearn.autolog()

# Load data from Delta Lake table
df = spark.read.format("delta").table("workspace.workshop.merchant_credit_card_transactions")

# Convert necessary columns to appropriate data types
df = df.withColumn("timestamp", F.to_timestamp("timestamp")) \
       .withColumn("card_bin", df["card_bin"].cast(IntegerType())) \
       .withColumn("bill_value", df["bill_value"].cast(DoubleType())) \
       .withColumn("installments", df["installments"].cast(IntegerType())) \
       .withColumn("card_expiration_date", F.last_day(F.to_date("card_expiration_date", "MM/yy")))

In [ ]:
display(df)

transaction_id transaction_type timestamp merchant_type merchant_name card_holder currency card_network card_bin bill_value installments card_expiration_date 059674d4-7ad7-4f5d-b854-43c0b1358517 chargeback 2024-07-09T20:37:00.813Z movies RioFilme Steven Jones GMD Visa 4 -56.457091882204296 1 2030-11-30 cbc3b982-e79a-457f-adf2-df4b7f113687 expense 2024-07-10T07:37:00.813Z retail Centauro Michael Williams LBP Mastercard 52 165.5620176701797 1 2031-12-31 37b88d4d-38e2-4212-b343-4bf58b0a44b1 chargeback 2024-06-13T23:37:00.813Z movies Orient Cinemas Kathryn Watson MMK Visa 4 -73.49020058546755 2 2031-01-31 41fee33b-844e-4d87-b36a-0db4e5b8b822 expense 2024-06-30T04:37:00.814Z restaurants Riqs Burguer Shop Daniel Jackson PLN Amex 34 307.52023524784374 1 2031-01-31 cc03bf4c-23b4-4b22-9b05-c62fc200e6d1 expense 2024-07-18T16:50:00.814Z restaurants Bistro Bar Vila Olímpia Rebecca Wilson BHD Elo 438935 85.06101397559685 1 2026-06-30 93943ad0-70a8-41c9-922e-29f618a2a98e chargeback 2024-06-07T10:37:00.814Z restaurants Allora Vino e Birra Mary Ingram ILS Visa 4 -149.13418876728886 1 2025-10-31 c714f1c3-745a-40fe-bc81-bc93c2b8cf68 chargeback 2024-05-03T13:37:00.814Z retail MadeiraMadeira Jerry Edwards GEL Mastercard 52 -274.67945432409556 1 2030-07-31 24ef3e16-4d70-495a-8086-3981a9808f21 chargeback 2024-07-17T00:37:00.815Z retail Shopee Rachael Porter KZT Visa 4 -401.7714770938127 1 2033-12-31 086ace30-3e9e-4819-b3d9-4f2b22aa5069 expense 2024-05-21T23:37:00.815Z retail Loja Integrada Erik Lee NAD Mastercard 53 258.72431231145396 3 2034-04-30 9cebff32-66bd-4b90-af6d-b917872e1b10 expense 2024-06-28T11:37:00.815Z retail Via Varejo Jay Reyes USD Amex 37 258.2658749989462 1 2031-07-31 94f8efd9-68b4-46c8-92dd-55d76af57f1e expense 2024-07-05T14:37:00.815Z restaurants Mais Burguinho Laurie Jones SRD Mastercard 54 143.04951157951126 1 2028-06-30 ea6d57bf-4d64-4e39-8121-769f507669f6 chargeback 2024-04-21T02:37:00.815Z drugstore_and_aesthetics Clamed Farmácias/Drogaria Caterinense Gina Perez LSL Elo 4576 -67.1844876436349 1 2030-11-30 3fdf9a9a-d11f-480b-bdb2-bce98dbd9d06 expense 2024-06-13T16:37:00.816Z retail Magalu Stephanie Poole NAD Visa 4 185.43408309835087 1 2032-10-31 1bbaa514-9dfc-4b84-a0fd-7e3f6fa1d2b3 expense 2024-07-06T20:37:00.816Z drugstore_and_aesthetics Panvel Farmácias Casey Perez YER Elo 5067 57.05573730077399 1 2024-11-30 2b326637-be4f-4b14-926f-37d4d021eb7d expense 2024-05-27T02:37:00.816Z retail B2W Americanas Donald Woods ZAR Mastercard 51 53.32420522578737 1 2032-03-31 40b0216d-7e75-475a-97f7-3e76ffd53322 expense 2024-06-08T20:37:00.816Z drugstore_and_aesthetics RaiaDrogasil Alexandria Watts BOB Elo 636297 117.91794431146091 1 2031-02-28 5622e36a-ebf7-4be2-969d-e33d86d57401 expense 2024-07-02T06:37:00.817Z drugstore_and_aesthetics Natura&Co Jessica Mcgee TMT Amex 37 45.38610417655615 2 2025-11-30 15a43f7b-a33d-4d6d-ba21-a093637db79c expense 2024-07-06T04:37:00.817Z retail Amazon Richard Walker AOA Mastercard 52 142.6146426573146 1 2029-01-31 dcbae8da-7c3e-425b-acc1-ca189825038f expense 2024-05-09T12:37:00.817Z drugstore_and_aesthetics Extrafarma Stacy Cortez MZN Elo 451416 97.95912379770456 1 2028-02-29 ee355cd5-d29f-4161-80e4-355649b14961 expense 2024-04-19T23:37:00.817Z retail Amazon Joseph Cox ZMW Elo 5067 81.96715617557219 1 2028-10-31 bed522e9-dfb6-4fad-bf5a-885603705fa4 expense 2024-05-25T11:37:00.818Z retail Atacado.com Kristy Wright JOD Visa 4 314.3887135578534 1 2026-02-28 8e0b0829-3bb6-446e-9f78-7b8fe525c9e9 chargeback 2024-05-25T11:37:00.818Z movies H2O Films Alexander Smith XAF Elo 4576 -108.59795587772624 1 2030-09-30 b2245270-d05b-4c63-80b2-b11d18bb9c61 chargeback 2024-07-03T19:37:00.818Z movies Kinoplex Kathryn Craig CVE Amex 34 -68.07204069569579 1 2027-06-30 86a3739c-934d-484d-8c6b-f5309f306b3f expense 2024-06-22T21:37:00.818Z movies Box Cinemas Steve Perez OMR Mastercard 54 23.053457090350122 3 2033-04-30 00630717-ea41-4cb3-b917-51c156cc371b chargeback 2024-06-25T21:37:00.818Z retail Shopfácil William Mcguire ERN 

In [ ]:
# Add is_fraud column (for the sake of the example, randomly assigning fraud status)
# In real scenarios, you would have actual labels for fraud detection
df = df.withColumn("is_fraud", F.rand() > 0.95)
display(df)

transaction_id transaction_type timestamp merchant_type merchant_name card_holder currency card_network card_bin bill_value installments card_expiration_date is_fraud 059674d4-7ad7-4f5d-b854-43c0b1358517 chargeback 2024-07-09T20:37:00.813Z movies RioFilme Steven Jones GMD Visa 4 -56.457091882204296 1 2030-11-30 false cbc3b982-e79a-457f-adf2-df4b7f113687 expense 2024-07-10T07:37:00.813Z retail Centauro Michael Williams LBP Mastercard 52 165.5620176701797 1 2031-12-31 false 37b88d4d-38e2-4212-b343-4bf58b0a44b1 chargeback 2024-06-13T23:37:00.813Z movies Orient Cinemas Kathryn Watson MMK Visa 4 -73.49020058546755 2 2031-01-31 false 41fee33b-844e-4d87-b36a-0db4e5b8b822 expense 2024-06-30T04:37:00.814Z restaurants Riqs Burguer Shop Daniel Jackson PLN Amex 34 307.52023524784374 1 2031-01-31 false cc03bf4c-23b4-4b22-9b05-c62fc200e6d1 expense 2024-07-18T16:50:00.814Z restaurants Bistro Bar Vila Olímpia Rebecca Wilson BHD Elo 438935 85.06101397559685 1 2026-06-30 false 93943ad0-70a8-41c9-922e-29f618a2a98e chargeback 2024-06-07T10:37:00.814Z restaurants Allora Vino e Birra Mary Ingram ILS Visa 4 -149.13418876728886 1 2025-10-31 false c714f1c3-745a-40fe-bc81-bc93c2b8cf68 chargeback 2024-05-03T13:37:00.814Z retail MadeiraMadeira Jerry Edwards GEL Mastercard 52 -274.67945432409556 1 2030-07-31 false 24ef3e16-4d70-495a-8086-3981a9808f21 chargeback 2024-07-17T00:37:00.815Z retail Shopee Rachael Porter KZT Visa 4 -401.7714770938127 1 2033-12-31 false 086ace30-3e9e-4819-b3d9-4f2b22aa5069 expense 2024-05-21T23:37:00.815Z retail Loja Integrada Erik Lee NAD Mastercard 53 258.72431231145396 3 2034-04-30 false 9cebff32-66bd-4b90-af6d-b917872e1b10 expense 2024-06-28T11:37:00.815Z retail Via Varejo Jay Reyes USD Amex 37 258.2658749989462 1 2031-07-31 false 94f8efd9-68b4-46c8-92dd-55d76af57f1e expense 2024-07-05T14:37:00.815Z restaurants Mais Burguinho Laurie Jones SRD Mastercard 54 143.04951157951126 1 2028-06-30 false ea6d57bf-4d64-4e39-8121-769f507669f6 chargeback 2024-04-21T02:37:00.815Z drugstore_and_aesthetics Clamed Farmácias/Drogaria Caterinense Gina Perez LSL Elo 4576 -67.1844876436349 1 2030-11-30 false 3fdf9a9a-d11f-480b-bdb2-bce98dbd9d06 expense 2024-06-13T16:37:00.816Z retail Magalu Stephanie Poole NAD Visa 4 185.43408309835087 1 2032-10-31 false 1bbaa514-9dfc-4b84-a0fd-7e3f6fa1d2b3 expense 2024-07-06T20:37:00.816Z drugstore_and_aesthetics Panvel Farmácias Casey Perez YER Elo 5067 57.05573730077399 1 2024-11-30 false 2b326637-be4f-4b14-926f-37d4d021eb7d expense 2024-05-27T02:37:00.816Z retail B2W Americanas Donald Woods ZAR Mastercard 51 53.32420522578737 1 2032-03-31 false 40b0216d-7e75-475a-97f7-3e76ffd53322 expense 2024-06-08T20:37:00.816Z drugstore_and_aesthetics RaiaDrogasil Alexandria Watts BOB Elo 636297 117.91794431146091 1 2031-02-28 false 5622e36a-ebf7-4be2-969d-e33d86d57401 expense 2024-07-02T06:37:00.817Z drugstore_and_aesthetics Natura&Co Jessica Mcgee TMT Amex 37 45.38610417655615 2 2025-11-30 false 15a43f7b-a33d-4d6d-ba21-a093637db79c expense 2024-07-06T04:37:00.817Z retail Amazon Richard Walker AOA Mastercard 52 142.6146426573146 1 2029-01-31 false dcbae8da-7c3e-425b-acc1-ca189825038f expense 2024-05-09T12:37:00.817Z drugstore_and_aesthetics Extrafarma Stacy Cortez MZN Elo 451416 97.95912379770456 1 2028-02-29 false ee355cd5-d29f-4161-80e4-355649b14961 expense 2024-04-19T23:37:00.817Z retail Amazon Joseph Cox ZMW Elo 5067 81.96715617557219 1 2028-10-31 false bed522e9-dfb6-4fad-bf5a-885603705fa4 expense 2024-05-25T11:37:00.818Z retail Atacado.com Kristy Wright JOD Visa 4 314.3887135578534 1 2026-02-28 false 8e0b0829-3bb6-446e-9f78-7b8fe525c9e9 chargeback 2024-05-25T11:37:00.818Z movies H2O Films Alexander Smith XAF Elo 4576 -108.59795587772624 1 2030-09-30 false b2245270-d05b-4c63-80b2-b11d18bb9c61 chargeback 2024-07-03T19:37:00.818Z movies Kinoplex Kathryn Craig CVE Amex 34 -68.07204069569579 1 2027-06-30 false 86a3739c-934d-484d-8c6b-f5309f306b3f expense 2024-06-22T21:37:00.818Z movies Box Cinemas Steve Perez OMR Mastercar

In [ ]:
# Convert Spark DataFrame to Pandas DataFrame for sklearn compatibility
pdf = df.toPandas()

# Feature Engineering
pdf['day_of_week'] = pdf['timestamp'].dt.dayofweek
pdf['hour_of_day'] = pdf['timestamp'].dt.hour
pdf['days_to_expiry'] = (pd.to_datetime(pdf['card_expiration_date']) - pd.Timestamp.now()).dt.days

# Encoding categorical variables
pdf = pdf.drop(columns=["merchant_name"])
pdf = pd.get_dummies(pdf, columns=['merchant_type', 'card_network', 'transaction_type'])

# Assuming you have a column `is_fraud` indicating whether the transaction is fraudulent
X = pdf.drop(columns=['transaction_id', 'timestamp', 'card_holder', 'currency', 'card_expiration_date', 'is_fraud'])
y = pdf['is_fraud']

# Split the data
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)

In [ ]:
# Define the experiment name
mlflow.set_experiment("/<SU NOMBRE>")

with mlflow.start_run():
    # Train the model
    clf = RandomForestClassifier(n_estimators=100, random_state=42)
    clf.fit(X_train, y_train)

    # Evaluate the model
    y_pred = clf.predict(X_test)
    y_prob = clf.predict_proba(X_test)[:, 1]

    # Display evaluation metrics
    print(classification_report(y_test, y_pred))
    print(f"ROC AUC Score: {roc_auc_score(y_test, y_prob)}")

2024/07/18 17:24:41 WARNING mlflow.utils.autologging_utils: MLflow autologging encountered a warning: "/local_disk0/.ephemeral_nfs/envs/pythonEnv-5955b124-1490-4546-aadb-da7d91e20c53/lib/python3.10/site-packages/mlflow/types/utils.py:406: UserWarning: Hint: Inferred schema contains integer column(s). Integer columns in Python cannot represent missing values. If your input data contains missing values at inference time, it will be encoded as floats and will cause a schema enforcement error. The best way to avoid this problem is to infer the model schema based on a realistic data sample (training dataset) that includes missing values. Alternatively, you can declare integer columns as doubles (float64) whenever these columns may have missing values. See `Handling Integers With Missing Values <https://www.mlflow.org/docs/latest/models.html#handling-integers-with-missing-values>`_ for more details."
2024/07/18 17:24:43 WARNING mlflow.utils.autologging_utils: MLflow autologging encountered a

              precision    recall  f1-score   support

       False       0.96      1.00      0.98      1283
        True       0.00      0.00      0.00        51

    accuracy                           0.96      1334
   macro avg       0.48      0.50      0.49      1334
weighted avg       0.92      0.96      0.94      1334

ROC AUC Score: 0.5110723946632433


In [ ]:
# Real-time prediction example
def predict_fraud(transaction):
    transaction = pd.DataFrame([transaction])
    transaction['timestamp'] = pd.to_datetime(transaction['timestamp'])
    transaction['day_of_week'] = transaction['timestamp'].dt.dayofweek
    transaction['hour_of_day'] = transaction['timestamp'].dt.hour
    transaction['days_to_expiry'] = (pd.to_datetime(transaction['card_expiration_date']) - pd.Timestamp.now()).dt.days
    transaction = pd.get_dummies(transaction, columns=['transaction_type', 'merchant_type', 'merchant_name', 'card_network'])
    transaction = transaction.reindex(columns=X_train.columns, fill_value=0)
    return clf.predict(transaction)

# Example transaction to predict
new_transaction = {
    'transaction_id': 123456,
    'transaction_type': 'purchase',
    'timestamp': '2024-07-18 12:34:56',
    'merchant_type': 'electronics',
    'merchant_name': 'Best Buy',
    'card_holder': 'John Doe',
    'currency': 'USD',
    'card_network': 'Visa',
    'card_bin': 123456,
    'bill_value': 199.99,
    'installments': 1,
    'card_expiration_date': '2025-12-31'
}

print(f'Is fraudulent: {predict_fraud(new_transaction)[0]}')

2024/07/18 17:25:00 WARNING mlflow.utils.autologging_utils: MLflow autologging encountered a warning: "/local_disk0/.ephemeral_nfs/envs/pythonEnv-5955b124-1490-4546-aadb-da7d91e20c53/lib/python3.10/site-packages/mlflow/types/utils.py:406: UserWarning: Hint: Inferred schema contains integer column(s). Integer columns in Python cannot represent missing values. If your input data contains missing values at inference time, it will be encoded as floats and will cause a schema enforcement error. The best way to avoid this problem is to infer the model schema based on a realistic data sample (training dataset) that includes missing values. Alternatively, you can declare integer columns as doubles (float64) whenever these columns may have missing values. See `Handling Integers With Missing Values <https://www.mlflow.org/docs/latest/models.html#handling-integers-with-missing-values>`_ for more details."


Is fraudulent: False


In [ ]:
import mlflow
catalog = "workspace"
schema = "workshop"
model_name = "<SU NOMBRE>-model"
mlflow.set_registry_uri("databricks-uc")
mlflow.register_model(
    model_uri="runs:/<ID RUN>/model",
    name=f"{catalog}.{schema}.{model_name}"
)

Successfully registered model 'workspace.workshop.piero_model'.
Created version '1' of model 'workspace.workshop.piero_model'.


<ModelVersion: aliases=[], creation_timestamp=1721323663629, current_stage=None, description='', last_updated_timestamp=1721323667677, name='workspace.workshop.piero_model', run_id='c878c1d96d9b40769f64a50a2fd69f42', run_link=None, source='dbfs:/databricks/mlflow-tracking/2975830249718483/c878c1d96d9b40769f64a50a2fd69f42/artifacts/model', status='READY', status_message='', tags={}, user_id='piero.ocampo@databricks.com', version='1'>